In [1]:


from SBLMDCOVDOCK.SBLSettings import DOCKING_Settings
from SBLMDCOVDOCK.md_setuptools import plot_xvg
import pickle
from copy import deepcopy
import subprocess

import pandas as pd
import os
import glob

# import gmxapi as gmx
import subprocess
import matplotlib.pyplot as plt

settings = DOCKING_Settings()
main_dir = os.getcwd()
import shutil

# AMPC - https://journals.asm.org/doi/10.1128/AAC.02073-20
ampc = "6T3D"
# KPC-2 - BLDB: http://dx.doi.org/10.1021/ACS.JMEDCHEM.7B00158
kpc2 = "5UL8"
# OXA-10 - BLDB: https://www.pnas.org/doi/full/10.1073/pnas.241442898
oxa10 = "1K55"

structures = pd.DataFrame({"PDBID": [ampc, kpc2, oxa10], 
                           "Name": ["AmpC", "KPC2", "OXA10"],
                           "Cat_Ser": [64, 70, 67],
                           "start": [4, 23, 21]})
                           

topo_dir  = os.path.join(settings.topology,settings.parent)
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"

settings.trial_name = "covalent"
print(os.getcwd())

/home/alexi/Documents/SBL_MD_CovDock


In [2]:
for pdb in structures.PDBID:
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    os.makedirs(data_dir, exist_ok=True)
    # gro_file = "APO_" +pdb + "_npt" + ".gro"
    pdb_file =  "APO_" +pdb + "_npt" + ".pdb"
    pdb_path = os.path.join(topo_dir, pdb_file)
    out_path = os.path.join(data_dir, pdb_file)
    # print(gro_path)
    # print(out_path)
    
    shutil.copy(pdb_path, out_path)


In [3]:
#2. Generate PDBQT files for protein
# break
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"
# print(dir)
for pdb in structures.PDBID:
    # break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)

    script_name = 'prepare_receptor4.py'
    prepare_rec_path = os.path.join(*[".."]*4,os.path.join(settings.config, settings.parent, script_name))
    pdb_file =  "APO_" +pdb + "_npt" + ".pdb"
    # pdb_file =  "APO_" +pdb + "_chimeraFH" + ".pdb"

    pdb_path = os.path.join(data_dir, pdb_file)
    cat_ser = str(structures[structures.PDBID == pdb].Cat_Ser.values[0])
    start = str(structures[structures.PDBID == pdb].start.values[0])
    out_pdb_name = "APO_" +pdb + "_ADT" + ".pdb" # extract from MD
    out_pdb_path = os.path.join(data_dir, out_pdb_name)
    print(start)
    # out_pdb_path = os.path.join(data_dir, out_pdb_name)
    # renumber residues
    res_to_remove = ["SOL","NA","CL"]
    string_to_remove = ",".join(res_to_remove)
    print(string_to_remove)
    !pdb_reres -$start $pdb_path > $out_pdb_path



    pdbqt_name = out_pdb_name.replace(".pdb", ".pdbqt")


    prepare_receptor_command = [pythonsh, prepare_rec_path,
                                "-r", pdb_file,
                                "-o", pdbqt_name,
                                "-e", 

                                "-A", "bonds_hydrogens",
                                "-U", "nphs_lps",
                                "-v",
                                ]

    print(" ".join(prepare_receptor_command))
    subprocess.run(prepare_receptor_command, cwd = data_dir,check=True)

    # re res pdbqt file - add value in structures.start to res number
    pdbqt_path = os.path.join(data_dir, pdbqt_name)

    with open(pdbqt_path, "r") as f:
        lines = f.readlines()


        new_lines = []
        for line in lines:
            if line.startswith("ATOM") or line.startswith("HETATM"):
                print(line)
                res_num = int(line[23:26])
                res_nus_string = line[23:26]
                new_res_num = res_num + int(start)
                # add new resnum to line but justifying to the right
                new_res_num_string = str(new_res_num).rjust(3)
                print(new_res_num_string)
                new_line = line.replace(res_nus_string, new_res_num_string)
                print(new_line)
            new_lines.append(new_line)

        # f.seek(0)
        # f.writelines(new_lines)
        # f.truncate()

4
SOL,NA,CL
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh ../../../../config/Dock/prepare_receptor4.py -r APO_6T3D_npt.pdb -o APO_6T3D_ADT.pdbqt -e -A bonds_hydrogens -U nphs_lps -v
set verbose to  True
read  APO_6T3D_npt.pdb
setting up RPO with mode= automatic and outputfilename=  APO_6T3D_ADT.pdbqt
charges_to_add= gasteiger
delete_single_nonstd_residues= True
adding gasteiger charges to peptide
'Deleting non-standard residues: from APO_6T3D_npt
ATOM      1  N   ALA     1      63.880  30.380  33.340  0.00  0.00    -0.067 N 

  5
ATOM      5  N   ALA     5      63.880  30.380  33.340  0.00  0.00    -0.067 N 

ATOM      2  CA  ALA     1      62.490  30.130  33.000  0.00  0.00     0.271 C 

  5
ATOM      2  CA  ALA     5      62.490  30.130  33.000  0.00  0.00     0.271 C 

ATOM      3  C   ALA     1      62.270  29.290  31.800  0.00  0.00     0.250 C 

  5
ATOM      3  C   ALA     5      62.270  29.290  31.800  0.00  0.00     0.250 C 

ATOM      4  O   ALA     1      63.1

In [4]:
import os
import subprocess

sdf_complex_dir = os.path.join(settings.structures_output, "Ligand_Complex")
for idx, row in structures.iterrows():

    break
    pdb = row["PDBID"]
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)

    cat_ser = row["Cat_Ser"]
    pdb_file =  "APO_" +pdb + "_ADT" + ".pdb" # extract from MD
    pdb_file = os.path.join(data_dir, pdb_file)
    ser_pdb =  "APO_" +pdb + "_ADT" + "_SER"+".pdb" # extract from MD
    ser_out = os.path.join(data_dir, ser_pdb)
    print(pdb_file, ser_pdb)

    # extract the serine from the receptor using subprocess

    !pdb_selres -$cat_ser $pdb_file | pdb_reatom | pdb_tidy > $ser_out
    # subprocess.run(["pdb_selres", "-"+str(cat_ser), pdb_file], cwd=data_dir,check=True)
    
    sdf_out = ser_pdb.replace(".pdb", ".sdf")
    # convert the serine to SDF and protonate it using subprocess
    subprocess.run(["obabel", ser_pdb, "-O", sdf_out], cwd=data_dir,check=True)


data/Dock/covalent/6T3D/APO_6T3D_ADT.pdb APO_6T3D_ADT_SER.pdb
data/Dock/covalent/5UL8/APO_5UL8_ADT.pdb APO_5UL8_ADT_SER.pdb


1 molecule converted


data/Dock/covalent/1K55/APO_1K55_ADT.pdb APO_1K55_ADT_SER.pdb


1 molecule converted
1 molecule converted


In [5]:
sdf_complex_dir = os.path.join(settings.structures_output, "Ligand_Complex")
# sdf_complex_out = os.path.join(settings.structures_output, "Complex_Aligned")
# break
os.makedirs(sdf_complex_dir, exist_ok=True)
# perform mcs alignment for each pdb and ligand
# need to extract coordinates and then apply these to the ligand files
for pdb in structures.PDBID:
    # pdb = "6T3D"

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    os.makedirs(sdf_complex_out, exist_ok=True)

    for lig in os.listdir(sdf_complex_dir):
        print(lig)
        lig_sdf = lig 
        lig = lig.replace(".sdf", "").split("_")[0]

        sdf_out = f"{pdb}_SER_{lig}.sdf"
        template_ser_sdf = "APO_" +pdb + "_ADT" + "_SER"+".sdf" # extract from MD
        template_ser_sdf_path = os.path.join(data_dir, template_ser_sdf)  

        lig_sdf = os.path.join(sdf_complex_dir, lig_sdf)
        sdf_out = os.path.join(sdf_complex_out, sdf_out)

        script_name = "mcs_constrained_alignment_SER.py"
        mcs_script_path = os.path.join(settings.config, settings.parent, script_name)
        mcs_command = [mcs_script_path,
                       template_ser_sdf_path,
                       lig_sdf,
                       sdf_out,
                       str(1), str(2), str(1), # default is 100??? # we only want one conformation
                       str(0)]
        
        print(" ".join(mcs_command))
        subprocess.run(mcs_command)
        # break
    # break

/home/alexi/miniconda3/envs/cudatoolkit_martini/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
[23:17:31] Molecule does not have explicit Hs. Consider calling AddHs()
[23:17:31] Molecule does not have explicit Hs. Consider calling AddHs()


PBC_6UQU.sdf
config/Dock/mcs_constrained_alignment_SER.py data/Dock/covalent/6T3D/APO_6T3D_ADT_SER.sdf prod_structures/Ligand_Substrate/Ligand_Complex/PBC_6UQU.sdf data/Dock/covalent/6T3D/Complex_Aligned/6T3D_SER_PBC.sdf 1 2 1 0
Writing conformation with RMS 0.056490 SIM 0.561299
Wrote 1 conformations for start_structures/Ligand_Substrate/Ligand_Complex_Stripped/PBC_6UQU.pdb
CXB_1NYM.sdf
config/Dock/mcs_constrained_alignment_SER.py data/Dock/covalent/6T3D/APO_6T3D_ADT_SER.sdf prod_structures/Ligand_Substrate/Ligand_Complex/CXB_1NYM.sdf data/Dock/covalent/6T3D/Complex_Aligned/6T3D_SER_CXB.sdf 1 2 1 0
Writing conformation with RMS 0.056857 SIM 0.715368
Wrote 1 conformations for start_structures/Ligand_Substrate/Ligand_Complex_Stripped/CXB_1NYM.pdb


/home/alexi/miniconda3/envs/cudatoolkit_martini/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
[23:17:31] Molecule does not have explicit Hs. Consider calling AddHs()
[23:17:31] Molecule does not have explicit Hs. Consider calling AddHs()


BX9_6JN4.sdf
config/Dock/mcs_constrained_alignment_SER.py data/Dock/covalent/6T3D/APO_6T3D_ADT_SER.sdf prod_structures/Ligand_Substrate/Ligand_Complex/BX9_6JN4.sdf data/Dock/covalent/6T3D/Complex_Aligned/6T3D_SER_BX9.sdf 1 2 1 0
Writing conformation with RMS 0.056908 SIM 0.733492
Wrote 1 conformations for start_structures/Ligand_Substrate/Ligand_Complex_Stripped/BX9_6JN4.pdb


/home/alexi/miniconda3/envs/cudatoolkit_martini/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
[23:17:31] Molecule does not have explicit Hs. Consider calling AddHs()
[23:17:31] Molecule does not have explicit Hs. Consider calling AddHs()


...

[23:19:44] Molecule does not have explicit Hs. Consider calling AddHs()
[23:19:44] Molecule does not have explicit Hs. Consider calling AddHs()
/home/alexi/miniconda3/envs/cudatoolkit_martini/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


0NB_4E3L.sdf
config/Dock/mcs_constrained_alignment_SER.py data/Dock/covalent/1K55/APO_1K55_ADT_SER.sdf prod_structures/Ligand_Substrate/Ligand_Complex/0NB_4E3L.sdf data/Dock/covalent/1K55/Complex_Aligned/1K55_SER_0NB.sdf 1 2 1 0


[23:19:44] Molecule does not have explicit Hs. Consider calling AddHs()
[23:19:44] Molecule does not have explicit Hs. Consider calling AddHs()
/home/alexi/miniconda3/envs/cudatoolkit_martini/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


Writing conformation with RMS 0.037562 SIM 0.746652
Wrote 1 conformations for start_structures/Ligand_Substrate/Ligand_Complex_Stripped/0NB_4E3L.pdb
BJP_1ERO.sdf
config/Dock/mcs_constrained_alignment_SER.py data/Dock/covalent/1K55/APO_1K55_ADT_SER.sdf prod_structures/Ligand_Substrate/Ligand_Complex/BJP_1ERO.sdf data/Dock/covalent/1K55/Complex_Aligned/1K55_SER_BJP.sdf 1 2 1 0
Writing conformation with RMS 0.037310 SIM 0.780022
Wrote 1 conformations for start_structures/Ligand_Substrate/Ligand_Complex_Stripped/BJP_1ERO.pdb


[23:19:44] Molecule does not have explicit Hs. Consider calling AddHs()
[23:19:44] Molecule does not have explicit Hs. Consider calling AddHs()


In [6]:
# convert comlplex SDF to PDB 
# change this to apply the coordinates from the aligned sdf files to the pdb version of the ligand
# sdf_complex_dir = os.path.join(settings.structures_output, "Ligand_Complex")
# sdf_complex_out = os.path.join(settings.structures_output, "Complex_Aligned")
# pdb_complex_out = os.path.join(settings.structures_output, "Aligned_PDB")
# re_res_complex = os.path.join(settings.structures_output, "Complex_ReRes")
# pdb_complex_in = os.path.join(settings.structures_input, "Ligand_Complex_Stripped")

# break

# Convert sdf to pdb
for pdb in structures.PDBID:
    # pdb = "6T3D"

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    pdb_complex_out = os.path.join(data_dir, "Aligned_PDB")
    re_res_complex = os.path.join(data_dir, "Complex_ReRes")
    pdb_complex_in = os.path.join(settings.structures_input, "Ligand_Complex_Stripped")





    os.makedirs(pdb_complex_out, exist_ok=True)
    os.makedirs(re_res_complex, exist_ok=True)
    os.makedirs(pdb_complex_in, exist_ok=True)



    for lig in os.listdir(sdf_complex_out):
        # break
        print(lig)

        pdb_name = lig.replace(".sdf", ".pdb")
        pdb_path = os.path.join(pdb_complex_in, pdb_name)

        sdf_path = os.path.join(sdf_complex_out, lig)
        # open sdf and extract coordinates


        # open pdb

        # replace pdb coordinates with those from sdf

        # save pdb to re_res_complex
        
    # break

    


6T3D_SER_0NB.sdf
6T3D_SER_AXL.sdf
6T3D_SER_DRW.sdf
6T3D_SER_SA2.sdf
6T3D_SER_CZ8.sdf
6T3D_SER_LOR.sdf
6T3D_SER_NFF.sdf
6T3D_SER_8CY.sdf
6T3D_SER_OZ9.sdf
6T3D_SER_N9X.sdf
6T3D_SER_0NE.sdf
6T3D_SER_2UL.sdf
6T3D_SER_1X6.sdf
6T3D_SER_OZO.sdf
6T3D_SER_L4C.sdf
6T3D_SER_JW8.sdf
6T3D_SER_WY4.sdf
6T3D_SER_AZR.sdf
6T3D_SER_3VT.sdf
6T3D_SER_ZXQ.sdf
6T3D_SER_9TJ.sdf
6T3D_SER_MXS.sdf
6T3D_SER_CED.sdf
6T3D_SER_LP0.sdf
6T3D_SER_3Y6.sdf
6T3D_SER_PBC.sdf
6T3D_SER_602.sdf
6T3D_SER_6V8.sdf
6T3D_SER_1OG.sdf
6T3D_SER_ALP.sdf
6T3D_SER_IPP.sdf
6T3D_SER_KL8.sdf
6T3D_SER_BJH.sdf
6T3D_SER_A1M.sdf
6T3D_SER_CEF.sdf
6T3D_SER_KCP.sdf
6T3D_SER_IAP.sdf
6T3D_SER_2TV.sdf
6T3D_SER_4J6.sdf
6T3D_SER_FOS.sdf
6T3D_SER_BO2.sdf
6T3D_SER_17O.sdf
6T3D_SER_BSH.sdf
6T3D_SER_0ND.sdf
6T3D_SER_KJK.sdf
6T3D_SER_BZB.sdf
6T3D_SER_3GE.sdf
6T3D_SER_A0Y.sdf
6T3D_SER_BSF.sdf
6T3D_SER_KCX.sdf
6T3D_SER_4CB.sdf
6T3D_SER_SM4.sdf
6T3D_SER_MOX.sdf
6T3D_SER_MXF.sdf
6T3D_SER_HD5.sdf
6T3D_SER_CD8.sdf
6T3D_SER_9CP.sdf
6T3D_SER_FK2.sdf
6T3D_SER_0N4.s

In [8]:
import os

# Assuming settings and other directory paths are defined above

# Function to extract coordinates from SDF file
def extract_coordinates_from_sdf(sdf_path):
    coords = []
    with open(sdf_path, 'r') as f:
        lines = f.readlines()
        atom_count = int(lines[3].strip().split()[0])
        for line in lines[4:4+atom_count]:
            x, y, z = line.split()[0:3]
            coords.append((x, y, z))
    return coords

# Function to replace coordinates in PDB file
def replace_coordinates_in_pdb(pdb_path, new_coords):
    new_content = []
    with open(pdb_path, 'r') as f:
        lines = f.readlines()
        coord_idx = 0
        for line in lines:
            if line.startswith("ATOM") or line.startswith("HETATM"):
                x, y, z = new_coords[coord_idx]
                coord_idx += 1
                new_line = f"{line[:30]}{float(x):8.3f}{float(y):8.3f}{float(z):8.3f}{line[54:]}"
                new_content.append(new_line)
            else:
                new_content.append(line)
    return new_content

# Loop through the ligands in the sdf_complex_out directory
for pdb in structures.PDBID:
    # pdb = "6T3D"

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    pdb_complex_out = os.path.join(data_dir, "Aligned_PDB")
    re_res_complex = os.path.join(data_dir, "Complex_ReRes")
    pdb_complex_in = os.path.join(settings.structures_input, "Ligand_Complex_Stripped")





    os.makedirs(pdb_complex_out, exist_ok=True)
    os.makedirs(re_res_complex, exist_ok=True)
    os.makedirs(pdb_complex_in, exist_ok=True)



    for lig in os.listdir(sdf_complex_out):    
        print(lig)
        ligcode = lig.split("_")[-1].replace(".sdf", "")
        print(ligcode)

        pdb_name = [x for x in os.listdir(pdb_complex_in) if ligcode in x][0]
        print(pdb_name)
        # print(sorted(os.listdir(pdb_complex_in)))
        pdb_path = os.path.join(pdb_complex_in, pdb_name)
        output_pdb_path = os.path.join(re_res_complex, lig.replace(".sdf", ".pdb"))
        sdf_path = os.path.join(sdf_complex_out, lig)
        # print(sorted(os.listdir(sdf_complex_out)))

        # Extract coordinates from SDF
        try:
            print("Extracting coordinates from SDF: ", lig)
            new_coords = extract_coordinates_from_sdf(sdf_path)
            try:
                print("Replacing coordinates in PDB: ", pdb_name)
                new_pdb_content = replace_coordinates_in_pdb(pdb_path, new_coords)
            except:
                print("Failed to replace coordinates in PDB")
                continue
            
        except:
            print("Failed to extract coordinates from SDF")
            continue

            # Replace coordinates in PDB
            
        # Save modified PDB to re_res_complex directory
        with open(output_pdb_path, 'w') as f:
            f.writelines(new_pdb_content)
    # break

6T3D_SER_0NB.sdf
0NB
0NB_4E3L.pdb
Extracting coordinates from SDF:  6T3D_SER_0NB.sdf
Replacing coordinates in PDB:  0NB_4E3L.pdb
6T3D_SER_AXL.sdf
AXL
AXL_3N7W.pdb
Extracting coordinates from SDF:  6T3D_SER_AXL.sdf
Replacing coordinates in PDB:  AXL_3N7W.pdb
6T3D_SER_DRW.sdf
DRW
DRW_3IQA.pdb
Extracting coordinates from SDF:  6T3D_SER_DRW.sdf
Replacing coordinates in PDB:  DRW_3IQA.pdb
6T3D_SER_SA2.sdf
SA2
SA2_2H5S.pdb
Extracting coordinates from SDF:  6T3D_SER_SA2.sdf
Failed to extract coordinates from SDF
6T3D_SER_CZ8.sdf
CZ8
CZ8_3MXR.pdb
Extracting coordinates from SDF:  6T3D_SER_CZ8.sdf
Replacing coordinates in PDB:  CZ8_3MXR.pdb
6T3D_SER_LOR.sdf
LOR
LOR_1FCN.pdb
Extracting coordinates from SDF:  6T3D_SER_LOR.sdf
Replacing coordinates in PDB:  LOR_1FCN.pdb
6T3D_SER_NFF.sdf
NFF
NFF_3NCK.pdb
Extracting coordinates from SDF:  6T3D_SER_NFF.sdf
Replacing coordinates in PDB:  NFF_3NCK.pdb
6T3D_SER_8CY.sdf
8CY
8CY_5UJO.pdb
Extracting coordinates from SDF:  6T3D_SER_8CY.sdf
Replacing coordin

In [9]:
# re res all entries to 64
no_SER_atoms = 6





for pdb in structures.PDBID:
    # pdb = "6T3D"
    cat_ser = str(structures[structures.PDBID == pdb].Cat_Ser.values[0])

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    pdb_complex_out = os.path.join(data_dir, "Aligned_PDB")
    re_res_complex = os.path.join(data_dir, "Complex_ReRes")
    pdb_complex_in = os.path.join(settings.structures_input, "Ligand_Complex_Stripped")
    

    os.makedirs(pdb_complex_out, exist_ok=True)
    os.makedirs(re_res_complex, exist_ok=True)
    os.makedirs(pdb_complex_in, exist_ok=True)




    for lig in os.listdir(re_res_complex):
        # break
        lig_path = os.path.join(re_res_complex, lig)

        with open(lig_path, "r+") as f:
            lines = f.readlines()

            new_lines = []
            atom_counter = 0
            for line in lines:
                if line.startswith("ATOM") or line.startswith("HETATM"):
                    atom_counter += 1
                    print(atom_counter)
                    # print(line)
                    # replace resname
                    # line = line[:17] + "SER" + line[20:]
                    #replace HETATM
                    # line = line[:0] + "ATOM  " + line[6:]
                    # replace resnum
                    line = line[:24] + cat_ser + line[26:] ### check this
                    # print(line)
                    # print(atom_counter)
                    if atom_counter > no_SER_atoms-1:
                        atom_name = line[12:16]
                        element  = line[76:78]+"  "

                        if "CA" in atom_name:
                            print(atom_name, element)
                            atom_name = atom_name.replace("CA", "CR")
                            line = line[:12] + atom_name + line[16:] 
                            print(atom_name)
                        # print(line)

                # break
                new_lines.append(line)
        # break
        with open(lig_path, "w+") as f:
            print(lig_path)
            f.writelines(new_lines)
        print(lig_path)
    # break

1
2
3
4
5
6
7
 CAK  C  
 CRK
8
 CAI  C  
 CRI
9
 CAJ  C  
 CRJ
10
11
 CAY  C  
 CRY
12
 CAV  C  
 CRV
13
14
 CAU  C  
 CRU
15
 CAS  C  
 CRS
16
17
18
19
 CAZ  C  
 CRZ
20
21
 CAW  C  
 CRW
22
 CAC  C  
 CRC
23
24
 CAT  C  
 CRT
25
data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_DGF.pdb
data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_DGF.pdb
1
2
3
4
5
6
7
 CAA  C  
 CRA
8
 CAB  C  
 CRB
9
10
11
12
13
14
15
16
 CAJ  C  
 CRJ
17
 CAK  C  
 CRK
18
 CAL  C  
 CRL
19
 CAM  C  
 CRM
20
21
22
23
24
 CAR  C  
 CRR
25
 CAS  C  
 CRS
26
 CAT  C  
 CRT
27
 CAU  C  
 CRU
28
 CAV  C  
 CRV
29
 CAW  C  
 CRW
30
 CAX  C  
 CRX
31
 CAY  C  
 CRY
32
 CAZ  C  
 CRZ
33
data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_5R7.pdb
data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_5R7.pdb
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_CEF.pdb
data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_CEF.pdb
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
1

In [10]:
print(len(os.listdir(re_res_complex)))

170


In [11]:
import os
resn = "SER"

# Assuming you have a DataFrame named "structures" containing the necessary data
# and "pdbqt_complex_out" is the directory containing PDB files

for pdb in structures.PDBID:
    # pdb = "6T3D"
    cat_ser = str(structures[structures.PDBID == pdb].Cat_Ser.values[0])

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    pdb_complex_out = os.path.join(data_dir, "Aligned_PDB")
    re_res_complex = os.path.join(data_dir, "Complex_ReRes")
    pdb_complex_in = os.path.join(settings.structures_input, "Ligand_Complex_Stripped")



    for lig in os.listdir(pdb_complex_out):
        # break
        if lig.endswith('.pdb'):  # Make sure to process only PDB files
            print(lig)
            pdb_path = os.path.join(pdb_complex_out, lig)

            with open(pdb_path, "r+") as f:
                lines = f.readlines()

                new_lines = []
                new_residue_index = cat_ser  # Starting index for the modified residue numbers

                for line in lines:
                    # print(line)
                    if line.startswith("ATOM") or line.startswith("HETATM"):
                        atom_serial = int(line[6:11])
                        residue_index = int(line[22:26])
                        old_resname = line[17:20]
                        print(atom_serial, residue_index, old_resname)
                        print(line)
                        # Update residue name and residue number
                        if old_resname != resn and residue_index != cat_ser:
                            line = line[:17] + resn + line[20:]
                            line = line[:22] + str(new_residue_index).rjust(4) + line[26:]
                        print(line)   
                        new_lines.append(line)

                # Write modified lines back to the file
                f.seek(0)
                f.writelines(new_lines)
                f.truncate()
            # break
    # break
print("Residue renaming and numbering changes completed.")


Residue renaming and numbering changes completed.


In [12]:
#2. Generate PDBQT files for the ligands
# pdbqt_complex_out = os.path.join(settings.structures_output, "Aligned_PDBQT")
# ligand_complex_stripped = os.path.join(settings.structures_input, "Ligand_Complex_Stripped")

# break

script_name = 'prepare_receptor4.py'
prepare_rec_path = os.path.join(os.path.join(settings.config, settings.parent, script_name))
for pdb in structures.PDBID:
    # pdb = "6T3D"
    cat_ser = str(structures[structures.PDBID == pdb].Cat_Ser.values[0])

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    pdb_complex_out = os.path.join(data_dir, "Aligned_PDB")
    re_res_complex = os.path.join(data_dir, "Complex_ReRes")
    pdb_complex_in = os.path.join(data_dir, "Ligand_Complex_Stripped")
    pdbqt_complex_out = os.path.join(data_dir, "Aligned_PDBQT")
    os.makedirs(pdbqt_complex_out, exist_ok=True)

    for lig in os.listdir(re_res_complex):
        # break

        lig_path = os.path.join(re_res_complex, lig)

        with open(lig_path, "r+") as f:
            lines = f.readlines()

            new_lines = []
            for line in lines:
                if line.startswith("ATOM") or line.startswith("HETATM"):
                    print(line)
                    # replace resname
                    line = line[:17] + "SER" + line[20:]
                    # replace resnum
                    line = line[:24] + str(cat_ser) + line[26:]
                    #replace HETATM
                    # line = line[:0] + "ATOM  " + line[6:]
                    print(line)
                    
                new_lines.append(line)
        # continue
        with open(lig_path, "w+") as f:
            f.writelines(new_lines)
        print(lig_path)

        pdb_path = os.path.join(re_res_complex, lig)
        pdbqt_path = os.path.join(pdbqt_complex_out, lig.replace(".pdb", ".pdbqt"))

        prepapre_cov_lig_command = [pythonsh, prepare_rec_path,
                                    "-r", pdb_path,
                                    "-o", pdbqt_path,
                                    "-A", "bonds_hydrogens",
                                    "-v"]
        
        print(" ".join(prepapre_cov_lig_command))
        subprocess.run(prepapre_cov_lig_command)

    # break

ATOM     13  N   SER A  64      48.800  51.874  46.337  1.00 25.41      A    N

ATOM     13  N   SER A  64      48.800  51.874  46.337  1.00 25.41      A    N

ATOM     14  CA  SER A  64      47.448  51.383  46.543  1.00 27.10      A    C

ATOM     14  CA  SER A  64      47.448  51.383  46.543  1.00 27.10      A    C

ATOM     15  C   SER A  64      47.404  49.888  46.440  1.00 32.44      A    C

ATOM     15  C   SER A  64      47.404  49.888  46.440  1.00 32.44      A    C

ATOM     16  O   SER A  64      46.474  49.270  46.937  1.00 26.93      A    O

ATOM     16  O   SER A  64      46.474  49.270  46.937  1.00 26.93      A    O

ATOM     17  CB  SER A  64      46.516  52.003  45.509  1.00 31.95      A    C

ATOM     17  CB  SER A  64      46.516  52.003  45.509  1.00 31.95      A    C

ATOM     18  OG  SER A  64      46.159  53.332  45.873  1.00 30.70      A    O

ATOM     18  OG  SER A  64      46.159  53.332  45.873  1.00 30.70      A    O

HETATM   85  CRK DGF A  64      43.731  

Traceback (most recent call last):
  File "config/Dock/prepare_receptor4.py", line 172, in <module>
    delete_single_nonstd_residues=delete_single_nonstd_residues)    
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 558, in __init__
    version=version, delete_single_nonstd_residues=delete_single_nonstd_residues)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 124, in __init__
    self.repairMol(mol, self.repair_type_list)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 174, in repairMol
    self.newHs = self.addHydrogens(mol)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 187, in addHydrogens
    HB.addHydrogens(mol)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/MolKit/hydrogenBuilder.py", line 61, in addHydrogens
    b

set verbose to  True
read  data/Dock/covalent/6T3D/Complex_ReRes/6T3D_SER_1S6.pdb
setting up RPO with mode= automatic and outputfilename=  data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_1S6.pdbqt
charges_to_add= gasteiger
delete_single_nonstd_residues= None
adding gasteiger charges to peptide
ATOM      1  N   SER A  64      48.794  51.880  46.335  1.00 10.66      A    N

ATOM      1  N   SER A  64      48.794  51.880  46.335  1.00 10.66      A    N

ATOM      2  CA  SER A  64      47.444  51.386  46.544  1.00 10.36      A    C

ATOM      2  CA  SER A  64      47.444  51.386  46.544  1.00 10.36      A    C

ATOM      3  C   SER A  64      47.402  49.890  46.439  1.00 10.88      A    C

ATOM      3  C   SER A  64      47.402  49.890  46.439  1.00 10.88      A    C

ATOM      4  O   SER A  64      46.474  49.270  46.936  1.00 11.45      A    O

ATOM      4  O   SER A  64      46.474  49.270  46.936  1.00 11.45      A    O

ATOM      5  CB  SER A  64      46.512  52.008  45.512  1.00 12.26

Traceback (most recent call last):
  File "config/Dock/prepare_receptor4.py", line 172, in <module>
    delete_single_nonstd_residues=delete_single_nonstd_residues)    
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 558, in __init__
    version=version, delete_single_nonstd_residues=delete_single_nonstd_residues)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 124, in __init__
    self.repairMol(mol, self.repair_type_list)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 174, in repairMol
    self.newHs = self.addHydrogens(mol)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 187, in addHydrogens
    HB.addHydrogens(mol)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/MolKit/hydrogenBuilder.py", line 61, in addHydrogens
    b

set verbose to  True
read  data/Dock/covalent/1K55/Complex_ReRes/1K55_SER_TJ7.pdb
setting up RPO with mode= automatic and outputfilename=  data/Dock/covalent/1K55/Aligned_PDBQT/1K55_SER_TJ7.pdbqt
charges_to_add= gasteiger
delete_single_nonstd_residues= None
adding gasteiger charges to peptide
ATOM     31  N   SER A  67      39.455  35.075  33.219  1.00  7.72      A    N

ATOM     31  N   SER A  67      39.455  35.075  33.219  1.00  7.72      A    N

ATOM     32  CA  SER A  67      38.135  35.685  33.330  1.00 11.04      A    C

ATOM     32  CA  SER A  67      38.135  35.685  33.330  1.00 11.04      A    C

ATOM     33  C   SER A  67      38.080  36.550  34.554  1.00 10.98      A    C

ATOM     33  C   SER A  67      38.080  36.550  34.554  1.00 10.98      A    C

ATOM     34  O   SER A  67      37.036  37.087  34.894  1.00 10.52      A    O

ATOM     34  O   SER A  67      37.036  37.087  34.894  1.00 10.52      A    O

ATOM     35  CB  SER A  67      37.023  34.631  33.404  1.00 13.10

In [13]:
print(len(os.listdir(pdbqt_complex_out)))

169


In [14]:
#3. Generate flexible/rigid PDBQT files for both the ligands and the receptors
flex_out = os.path.join(settings.structures_output, "PDBQT_Flex")
rigid_out = os.path.join(settings.structures_output, "PDBQT_Rigid")

os.makedirs(flex_out, exist_ok=True)
os.makedirs(rigid_out, exist_ok=True)

# 3.1 Generate flex and rigid PDBQT files for the ligands
script_name = 'prepare_flexreceptor4.py'

prepare_flex_path = os.path.join(os.path.join(settings.config, settings.parent, script_name))


for pdb in structures.PDBID:
    # pdb = "6T3D"
    cat_ser = str(structures[structures.PDBID == pdb].Cat_Ser.values[0])

    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)
    # print(data_dir)
    sdf_complex_out = os.path.join(data_dir, "Complex_Aligned")
    pdb_complex_out = os.path.join(data_dir, "Aligned_PDB")
    re_res_complex = os.path.join(data_dir, "Complex_ReRes")
    pdb_complex_in = os.path.join(data_dir, "Ligand_Complex_Stripped")
    pdbqt_complex_out = os.path.join(data_dir, "Aligned_PDBQT")
    flex_out = os.path.join(data_dir, "PDBQT_Flex")
    rigid_out = os.path.join(data_dir, "PDBQT_Rigid")

    os.makedirs(flex_out, exist_ok=True)
    os.makedirs(rigid_out, exist_ok=True)
    
    for lig in os.listdir(pdbqt_complex_out):
    # break


        lig_path = os.path.join(pdbqt_complex_out, lig)

        flex_out_path = os.path.join(flex_out, lig)

        prepare_flex_lig_command = [pythonsh, prepare_flex_path,
                                    "-r", lig_path,
                                    "-s", "SER"+str(cat_ser),
                                    "-g", flex_out_path.replace(".pdbqt", "_rigid.pdbqt").replace("PDBQT_Flex", "PDBQT_Rigid"),
                                    "-x", flex_out_path.replace(".pdbqt", "_flex.pdbqt"),
                                    "-v"]


        print(" ".join(prepare_flex_lig_command))
        try:
            subprocess.run(prepare_flex_lig_command, check=True)
        except:
            print("Error in", lig)
            pass
    # break


/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_APB.pdbqt -s SER64 -g data/Dock/covalent/6T3D/PDBQT_Rigid/6T3D_SER_APB_rigid.pdbqt -x data/Dock/covalent/6T3D/PDBQT_Flex/6T3D_SER_APB_flex.pdbqt -v
set verbose to True
read  data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_APB.pdbqt
Specified flexres selection strings are:
   SER64
selecting  SER64
res_names= ['SER64']
looking for   SER64
 added  ['SER64']  to  [<Residue instance> 6T3D_SER_APB:A:SER64 with 19 MolKit.molecule.Atom]
located  1  residues to format:
   6T3D_SER_APB:A:SER64
beginning formatting ...
finished!
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_M9W.pdbqt -s SER64 -g data/Dock/covalent/6T3D/PDBQT_Rigid/6T3D_SER_M9W_rigid.pdbqt -x data/Dock/covalent/6T3D/PDBQT_Flex/6T3D_SER_M9W_flex.pdbqt -v
set verbose to True
read  data/D

Traceback (most recent call last):
  File "config/Dock/prepare_flexreceptor4.py", line 185, in <module>
    non_rotatable_bonds=all_bnds)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 2674, in __init__
    flex_residues = self.flex_residues = self.process_residues(residues)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 3080, in process_residues
    ntors = self.setAutoFlexFields(res)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 3134, in setAutoFlexFields
    res.root = ca_atom[0]
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/lib/python2.7/UserList.py", line 31, in __getitem__
    def __getitem__(self, i): return self.data[i]
IndexError: list index out of range


Error in 6T3D_SER_4OV.pdbqt
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_DVR.pdbqt -s SER64 -g data/Dock/covalent/6T3D/PDBQT_Rigid/6T3D_SER_DVR_rigid.pdbqt -x data/Dock/covalent/6T3D/PDBQT_Flex/6T3D_SER_DVR_flex.pdbqt -v
set verbose to True
read  data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_DVR.pdbqt
Specified flexres selection strings are:
   SER64
selecting  SER64
res_names= ['SER64']
looking for   SER64
 added  ['SER64']  to  [<Residue instance> 6T3D_SER_DVR:A:SER64 with 37 MolKit.molecule.Atom]
located  1  residues to format:
   6T3D_SER_DVR:A:SER64
beginning formatting ...
finished!
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/6T3D/Aligned_PDBQT/6T3D_SER_0ND.pdbqt -s SER64 -g data/Dock/covalent/6T3D/PDBQT_Rigid/6T3D_SER_0ND_rigid.pdbqt -x data/Dock/covalent/6T3D/PDBQT_Flex/6T3D_SER_0ND_flex.pdbqt -v
set 

Traceback (most recent call last):
  File "config/Dock/prepare_flexreceptor4.py", line 185, in <module>
    non_rotatable_bonds=all_bnds)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 2674, in __init__
    flex_residues = self.flex_residues = self.process_residues(residues)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 3080, in process_residues
    ntors = self.setAutoFlexFields(res)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 3134, in setAutoFlexFields
    res.root = ca_atom[0]
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/lib/python2.7/UserList.py", line 31, in __getitem__
    def __getitem__(self, i): return self.data[i]
IndexError: list index out of range


read  data/Dock/covalent/5UL8/Aligned_PDBQT/5UL8_SER_ALP.pdbqt
Specified flexres selection strings are:
   SER70
selecting  SER70
res_names= ['SER70']
looking for   SER70
 added  ['SER70']  to  [<Residue instance> 5UL8_SER_ALP:A:SER70 with 27 MolKit.molecule.Atom]
located  1  residues to format:
   5UL8_SER_ALP:A:SER70
beginning formatting ...
finished!
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/5UL8/Aligned_PDBQT/5UL8_SER_HOQ.pdbqt -s SER70 -g data/Dock/covalent/5UL8/PDBQT_Rigid/5UL8_SER_HOQ_rigid.pdbqt -x data/Dock/covalent/5UL8/PDBQT_Flex/5UL8_SER_HOQ_flex.pdbqt -v
set verbose to True
read  data/Dock/covalent/5UL8/Aligned_PDBQT/5UL8_SER_HOQ.pdbqt
Specified flexres selection strings are:
   SER70
selecting  SER70
res_names= ['SER70']
looking for   SER70
 added  ['SER70']  to  [<Residue instance> 5UL8_SER_HOQ:A:SER70 with 29 MolKit.molecule.Atom]
located  1  residues to format:
   5UL8_SER_HOQ:A:SER70
beginni

Traceback (most recent call last):
  File "config/Dock/prepare_flexreceptor4.py", line 185, in <module>
    non_rotatable_bonds=all_bnds)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 2674, in __init__
    flex_residues = self.flex_residues = self.process_residues(residues)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 3080, in process_residues
    ntors = self.setAutoFlexFields(res)
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/CCSBpckgs/AutoDockTools/MoleculePreparation.py", line 3134, in setAutoFlexFields
    res.root = ca_atom[0]
  File "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/lib/python2.7/UserList.py", line 31, in __getitem__
    def __getitem__(self, i): return self.data[i]
IndexError: list index out of range


set verbose to True
read  data/Dock/covalent/1K55/Aligned_PDBQT/1K55_SER_SM4.pdbqt
Specified flexres selection strings are:
   SER67
selecting  SER67
res_names= ['SER67']
looking for   SER67
 added  ['SER67']  to  [<Residue instance> 1K55_SER_SM4:A:SER67 with 34 MolKit.molecule.Atom]
located  1  residues to format:
   1K55_SER_SM4:A:SER67
beginning formatting ...
finished!
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/1K55/Aligned_PDBQT/1K55_SER_1X6.pdbqt -s SER67 -g data/Dock/covalent/1K55/PDBQT_Rigid/1K55_SER_1X6_rigid.pdbqt -x data/Dock/covalent/1K55/PDBQT_Flex/1K55_SER_1X6_flex.pdbqt -v
set verbose to True
read  data/Dock/covalent/1K55/Aligned_PDBQT/1K55_SER_1X6.pdbqt
Specified flexres selection strings are:
   SER67
selecting  SER67
res_names= ['SER67']
looking for   SER67
 added  ['SER67']  to  [<Residue instance> 1K55_SER_1X6:A:SER67 with 26 MolKit.molecule.Atom]
located  1  residues to format:
   1K55_SER

In [18]:
print(len(os.listdir(flex_out)))

169


In [19]:

# break
# 3.2 Generate flex and rigid PDBQT files for the receptors

for pdb in structures.PDBID:
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)

    break
    # pdb = "6T3D"
    cat_ser = structures[structures.PDBID == pdb].Cat_Ser.values[0]

    # pdb_file = f"APO_{pdb}_chimeraFH.pdb"




    out_pdb_name = "APO_" +pdb + "_ADT" + ".pdb"
    pdbqt_name = out_pdb_name.replace(".pdb", ".pdbqt")

    pdbqt_path = os.path.join(data_dir, pdbqt_name)

    prepare_flex_rec_command = [pythonsh, prepare_flex_path,
                                "-r", pdbqt_path,
                                "-s", "SER"+str(cat_ser),
                                "-g", pdbqt_path.replace(".pdbqt", "_rigid.pdbqt"),
                                "-x", pdbqt_path.replace(".pdbqt", "_flex.pdbqt"),
                                "-v"]

    print(" ".join(prepare_flex_rec_command))
    subprocess.run(prepare_flex_rec_command,check=True)
    # break

/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/6T3D/APO_6T3D_ADT.pdbqt -s SER64 -g data/Dock/covalent/6T3D/APO_6T3D_ADT_rigid.pdbqt -x data/Dock/covalent/6T3D/APO_6T3D_ADT_flex.pdbqt -v
set verbose to True
read  data/Dock/covalent/6T3D/APO_6T3D_ADT.pdbqt
Specified flexres selection strings are:
   SER64
selecting  SER64
res_names= ['SER64']
looking for   SER64
located  0  residues to format:
beginning formatting ...
finished!
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh config/Dock/prepare_flexreceptor4.py -r data/Dock/covalent/5UL8/APO_5UL8_ADT.pdbqt -s SER70 -g data/Dock/covalent/5UL8/APO_5UL8_ADT_rigid.pdbqt -x data/Dock/covalent/5UL8/APO_5UL8_ADT_flex.pdbqt -v
set verbose to True
read  data/Dock/covalent/5UL8/APO_5UL8_ADT.pdbqt
Specified flexres selection strings are:
   SER70
selecting  SER70
res_names= ['SER70']
looking for   SER70
located  0  residues to format:
beginning formatting ...
fini

In [20]:
for pdb in structures.PDBID:
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)

    break
    # pdb_name = "APO_" +pdb + "_ADT_flex" + ".pdbqt"

    # orig_path = os.path.join(dir, pdb_name)

    # dest_path = os.path.join(flex_out, pdb_name)
    # print(os.getcwd())
    # # copy files to the flex_out directory
    # shutil.copy(orig_path, dest_path)
    # print(orig_path, dest_path)

    flex_out = os.path.join(data_dir, "PDBQT_Flex")
    rigid_out = os.path.join(data_dir, "PDBQT_Rigid")

    pdb_name = "APO_" +pdb + "_ADT_rigid" + ".pdbqt"
    orig_path = os.path.join(data_dir, pdb_name)

    dest_path = os.path.join(flex_out, pdb_name)
    shutil.copy(orig_path, dest_path)
    print(orig_path, dest_path)
    


data/Dock/covalent/6T3D/APO_6T3D_ADT_rigid.pdbqt data/Dock/covalent/6T3D/PDBQT_Flex/APO_6T3D_ADT_rigid.pdbqt
data/Dock/covalent/5UL8/APO_5UL8_ADT_rigid.pdbqt data/Dock/covalent/5UL8/PDBQT_Flex/APO_5UL8_ADT_rigid.pdbqt
data/Dock/covalent/1K55/APO_1K55_ADT_rigid.pdbqt data/Dock/covalent/1K55/PDBQT_Flex/APO_1K55_ADT_rigid.pdbqt


In [30]:
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"
print(flex_out)

dir_indent = 5

# For the Borons
modified_param_line = "parameter_file "+ os.path.join(*[".."]*dir_indent,settings.config, 
                                                        settings.parent, 
                                                        "AD4.1_bound.dat") + "\n"



for pdb in structures.PDBID:

    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)

    flex_out = os.path.join(data_dir, "PDBQT_Flex")


    for lig in os.listdir(flex_out):

        if "_flex.pdbqt" not in lig:
            continue
        if "APO" in lig:
            continue
        if ".pdbqt" not in lig:
            continue

        # break
        print(pdb, lig)


        
        break
        print(os.getcwd())
        script_name = "prepare_gpf4.py"
        prepare_grid_path = os.path.join(*[".."]*dir_indent,os.path.join(settings.config, 
                                                                     settings.parent, 
                                                                     script_name))

        pdb_name = "APO_" +pdb + "_ADT_rigid" + ".pdb"
        pdbqt_name = pdb_name.replace(".pdb", ".pdbqt") #.replace("_flex", "_rigid")
        print(pdbqt_name)
        ligand_name = lig
        
        lig = lig.replace(".pdbqt", "")



        prep_grid_command = [pythonsh,
                            prepare_grid_path,
                            "-r", pdbqt_name,
                            "-l", ligand_name,
                            "-x", ligand_name,
                            "-o", lig + ".gpf", 
                            # "-p", "ligand_types='H,HD,HS,C,A,N,NA,NS,OA,OS,F,Mg,Mn,Zn,Ca,Fe,Cl,Br,I,SA,S,Se,P,GA,GC,GN,GO,GP,G'",
                            
                            "-v"]
        
        # print(" ".join(prep_grid_command))
        try:
            subprocess.run(prep_grid_command, cwd=flex_out)
            with open(os.path.join(flex_out, lig + ".gpf"), "r+") as f:
                lines = f.readlines()

                new_lines = []

                new_lines.append(modified_param_line)
                for line in lines:
                    new_lines.append(line)

                # Write modified lines back to the file
                f.seek(0)
                f.writelines(new_lines)
                f.truncate()            
        except:
            pass
    # break
    # break
# pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"



        subprocess.run(["touch", "empty"], cwd=flex_out, check=True)

# for lig in os.listdir(flex_out):
#     for pdb in structures.PDBID:
        print(os.getcwd())
        script_name = "prepare_dpf4.py"
        prepare_dock_path = os.path.join(*[".."]*dir_indent,os.path.join(settings.config, 
                                                                     settings.parent, 
                                                                     script_name))

        prep_dock_command = [pythonsh,
                            prepare_dock_path,
                            "-l", ligand_name,
                            "-x", ligand_name,
                            "-r", pdbqt_name,
                            "-o", lig+ ".dpf" ,
                            "-p", "move='empty'",
                            # "-p", "rmsdatoms='all'"
                            "-v"]

        # print(" ".join(prep_dock_command))

        # subprocess.run(prep_dock_command, cwd=flex_out, check=True)



        try:
            print(" ".join(prep_dock_command))
            # subprocess.run(prep_dock_command, cwd=flex_out, check=True)
            
            # with open(os.path.join(flex_out, lig + ".dpf"), "r+") as f:
            #     lines = f.readlines()

            #     new_lines = []

            #     new_lines.append(modified_param_line)                                                      
            #     for line in lines:
            #         if line.startswith("unbound_model"):
            #             line = "unbound_energy 0.0      # COVALENT " + "\n"
            #         new_lines.append(line)

            #     new_lines.append("rmsdatoms all     # COVALENT "+ "\n")

            #     # Write modified lines back to the file
            #     f.seek(0)
            #     f.writelines(new_lines)
            #     f.truncate()
        except:
            pass

    
            # break

data/Dock/covalent/1K55/PDBQT_Flex
6T3D 6T3D_SER_1S6_flex.pdbqt
/home/alexi/Documents/SBL_MD_CovDock
APO_6T3D_ADT_rigid.pdbqt
read  6T3D_SER_1S6_flex
end of getTypes: mol_types= A C OA N SA HD  class= <type 'str'>
set gpo.ligand_stem to 6T3D_SER_1S6_flex
set gpo.ligand_filename to 6T3D_SER_1S6_flex.pdbqt
set gpo.ligand_types to <type 'str'>
set npts to  [40, 40, 40]
set_receptor filename to  APO_6T3D_ADT_rigid.pdbqt
end of getTypes: mol_types= A C OA N SA HD  class= <type 'str'>
writing  6T3D_SER_1S6_flex.gpf
npts custom_parameter_file gridfld spacing receptor_types ligand_types receptor gridcenter smooth map elecmap dsolvmap dielectric4
/home/alexi/Documents/SBL_MD_CovDock
/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh ../../../../../config/Dock/prepare_dpf4.py -l 6T3D_SER_1S6_flex.pdbqt -x 6T3D_SER_1S6_flex.pdbqt -r APO_6T3D_ADT_rigid.pdbqt -o 6T3D_SER_1S6_flex.dpf -p move='empty' -v
6T3D 6T3D_SER_QFS_flex.pdbqt
/home/alexi/Documents/SBL_MD_CovDock
APO_6T3D_ADT_rigid.pd

In [28]:
# print number of dpf and gpf files
print(len(os.listdir(flex_out)))

print(len([x for x in os.listdir(flex_out) if x.endswith(".dpf")]))
print(len([x for x in os.listdir(flex_out) if x.endswith(".gpf")]))

339
168
1


In [ ]:
### https://www.researchgate.net/post/What_are_the_potential_shell_well_and_atomic_solvation_parameters_for_the_boron_atom

In [ ]:
# 5. Run AutoGrid and AutoDock



autodockgpu_dir = "/home/alexi/Documents/AutoDock-GPU/bin"
engine = "CUDA_64"

autodockgpu = f"autodock_{engine}wi"
auto_dock = os.path.join(autodockgpu_dir, autodockgpu)
docked = []
# for pdb in structures.PDBID:
for pdb in structures.PDBID:
    break
    data_dir = os.path.join(settings.data_directory, settings.parent, settings.trial_name, pdb)

    flex_out = os.path.join(data_dir, "PDBQT_Flex")
    for lig in os.listdir(flex_out):
        if "_flex.dpf" not in lig:
            continue
        lig = lig.replace(".dpf", "")
        print(lig)

    # for pdb in structures.PDBID:
        # print("Docking ", lig, " to ", pdb)
        name = "APO_" +pdb + "_ADT"+ "_rigid"
        pdb_name =  name + ".pdb"
        pdbqt_name = pdb_name.replace(".pdb", ".pdbqt")

        grid_name = lig +".gpf"
        grid_log = grid_name.replace(".gpf", ".glg")
        grid_log = f"{lig}_{name}.glg"


        autogrid_command = ["autogrid4", 
                            "-p", grid_name, 
                            "-l", grid_log, 
                            # "-d", f"{lig}_{name}.maps.fld",
                            # "-o", f"{lig}_{name}.maps.map",
        ]
                            # "-v"]

        dock_name = lig + ".dpf"
        dock_log = dock_name.replace(".dpf", ".dlg")

        autodock_command = [auto_dock, 
                            # "-p", dock_name, 
                            # "-l", dock_log, 
                            "-M",  f"{name}.maps.fld", 
                            "-L", f"{lig}.pdbqt",
                            "--lsmet", "ad",
                            # "--psize", "50",
                            # "--nrun", "50",
                            "-v"]


        dir = "/home/alexi/Documents/SBL_MD_CovDock/topology/Dock"
        # print(os.listdir(dir))
        try:
            subprocess.run(autogrid_command, check=True,cwd=flex_out)
            # subprocess.run(autodock_command, check=True,cwd=flex_out)        
            # check that the map fld contains ligand - otherwise command does not run before file is printed
            with open(os.path.join(flex_out, f"{name}.maps.fld"), "r") as f:
                lines = f.readlines()
                for line in lines:
                    if grid_name in line:
                        print(line)
                        print("Ligand in map fld")
                        # break
                        subprocess.run(autodock_command, check=True,cwd=flex_out)        
                        print("Docking successful")
                        docked.append((lig, pdb))
        except:
            pass
        
print(docked)

6T3D_SER_1X6_flex
#GRID_PARAMETER_FILE 6T3D_SER_1X6_flex.gpf

Ligand in map fld
AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11474 MB (total: 12022 MB)

CUDA Setup time 0.060830s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 1132076
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.002474s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 1132076 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 |   -0.21 kcal/mol |   -0.33 +/-    0.10 kcal/mol 


autogrid4: ERROR:  unknown ligand atom type Ru
add parameters for it to the parameter library first!




#GRID_PARAMETER_FILE 6T3D_SER_RM9_flex.gpf

Ligand in map fld
AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11474 MB (total: 12022 MB)

CUDA Setup time 0.045219s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 1132076
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.002933s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 1132076 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 |25670.28 kcal/mol |10841.37 +/- 3954.38 kcal/mol |       4 | 6010.6

In [ ]:
print(os.getcwd())

/home/alexi/Documents/SBL_MD_CovDock


In [ ]:
import os

def get_directory_details(directory_path):
    total_size = 0
    file_count = 0
    
    for dirpath, dirnames, filenames in os.walk(directory_path):
        for f in filenames:
            fp = os.path.join(dirpath, f)
            if not os.path.islink(fp):  # skip symbolic links
                total_size += os.path.getsize(fp)
            file_count += 1

    return file_count, total_size

directory_path = 'start_structures'
file_count, total_size = get_directory_details(directory_path)
print(f"Number of files: {file_count}")
print(f"Total size: {total_size} bytes")
print(f"Total size: {total_size / 1024**2} MB")

Number of files: 1281
Total size: 73588877 bytes
Total size: 70.17982196807861 MB
